## Overview

This notebook is intended to be used as teaching material for those who want initialy exposure to data engineering and machine learning. We go through basic data ingestion, pre-processing, organizing or data in the medallion lakeouse architecture (bronze, silverm, and gold layers), and some very basic machine learning.

##Read in data files

In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *

In [0]:
# CSV options for reading in csv files
file_type = "csv"
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# read list of airports data into a dataframe 
airports = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load("/FileStore/tables/airports_list.csv")

# read airport weather data into a dataframe 
airport_weather = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load("/FileStore/tables/airport_weather_2019.csv")



In [0]:
display(airports.sample(fraction=0.1))

ORIGIN_AIRPORT_ID DISPLAY_AIRPORT_NAME ORIGIN_CITY_NAME NAME 11259 Dallas Love Field Dallas, TX DALLAS FAA AIRPORT, TX US 12478 John F. Kennedy International New York, NY LAGUARDIA AIRPORT, NY US 12954 Long Beach Daugherty Field Long Beach, CA LOS ANGELES INTERNATIONAL AIRPORT, CA US 10693 Myrtle Beach International Myrtle Beach, SC NORTH MYRTLE BEACH, SC US 14831 San Jose International San Jose, CA SAN JOSE INTERNATIONAL AIRPORT, CA US 11292 Stapleton International Denver, CO DENVER INTERNATIONAL AIRPORT, CO US 13851 Will Rogers World Oklahoma City, OK OKLAHOMA CITY WILL ROGERS WORLD AIRPORT, OK US

In [0]:
display(airport_weather.sample(fraction=0.1))

STATION NAME DATE AWND PGTM PRCP SNOW SNWD TAVG TMAX TMIN WDF2 WDF5 WSF2 WSF5 WT01 WT02 WT03 WT04 WT05 WT06 WT07 WT08 WT09 WESD WT10 PSUN TSUN SN32 SX32 TOBS WT11 USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 1/17/2019 4.03 null 0.1 0.0 0.0 42.0 50.0 35.0 180.0 180.0 8.9 13.0 1.0 null 1.0 null null null null 1.0 null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 1/18/2019 2.91 null 0.0 0.0 0.0 50.0 58.0 47.0 220.0 220.0 8.1 10.1 1.0 null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2/3/2019 4.47 null 0.04 0.0 0.0 58.0 65.0 50.0 90.0 80.0 12.1 17.0 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2/6/2019 7.38 null 0.1 0.0 0.0 64.0 71.0 59.0 210.0 220.0 14.1 17.0 1.0 1.0 null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/4/2019 16.78 null 0.0 0.0 0.0 42.0 44.0 34.0 320.0 330.0 28.0 34.0 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/6/2019 11.18 null 0.0 0.0 0.0 35.0 47.0 27.0 330.0 320.0 21.0 29.1 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/12/2019 6.04 null 0.0 0.0 0.0 57.0 74.0 46.0 40.0 40.0 12.1 14.1 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/16/2019 12.75 null 0.0 0.0 0.0 49.0 52.0 43.0 340.0 310.0 23.9 28.0 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/22/2019 13.65 null 0.0 0.0 0.0 52.0 66.0 40.0 330.0 330.0 23.9 30.0 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/29/2019 4.7 null 0.0 0.0 0.0 61.0 73.0 49.0 220.0 260.0 13.0 17.0 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 3/31/2019 15.66 null 0.1 0.0 0.0 56.0 68.0 43.0 330.0 310.0 23.9 35.1 1.0 null 1.0 null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 4/8/2019 7.83 null 0.0 0.0 0.0 70.0 75.0 65.0 220.0 210.0 18.1 29.1 1.0 null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 4/21/2019 9.84 null 0.0 0.0 0.0 56.0 72.0 44.0 340.0 300.0 21.9 29.1 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 4/27/2019 7.83 null 0.0 0.0 0.0 64.0 78.0 49.0 240.0 220.0 15.0 19.9 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 5/12/2019 7.83 null 0.52 0.0 0.0 69.0 75.0 66.0 230.0 230.0 15.0 21.0 1.0 null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 5/13/2019 10.51 null 0.0 0.0 0.0 68.0 74.0 59.0 310.0 330.0 21.9 25.9 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 5/20/2019 6.71 null 0.0 0.0 0.0 78.0 87.0 71.0 300.0 300.0 16.1 21.9 null null null null null null null null null null null null null null null null null USW00013874 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 5/21/2019

In [0]:
airport_weather.columns

Out[5]: ['STATION',
 'NAME',
 'DATE',
 'AWND',
 'PGTM',
 'PRCP',
 'SNOW',
 'SNWD',
 'TAVG',
 'TMAX',
 'TMIN',
 'WDF2',
 'WDF5',
 'WSF2',
 'WSF5',
 'WT01',
 'WT02',
 'WT03',
 'WT04',
 'WT05',
 'WT06',
 'WT07',
 'WT08',
 'WT09',
 'WESD',
 'WT10',
 'PSUN',
 'TSUN',
 'SN32',
 'SX32',
 'TOBS',
 'WT11']

In [0]:
airport_weather.dtypes

Out[6]: [('STATION', 'string'),
 ('NAME', 'string'),
 ('DATE', 'string'),
 ('AWND', 'double'),
 ('PGTM', 'double'),
 ('PRCP', 'double'),
 ('SNOW', 'double'),
 ('SNWD', 'double'),
 ('TAVG', 'double'),
 ('TMAX', 'double'),
 ('TMIN', 'double'),
 ('WDF2', 'double'),
 ('WDF5', 'double'),
 ('WSF2', 'double'),
 ('WSF5', 'double'),
 ('WT01', 'double'),
 ('WT02', 'double'),
 ('WT03', 'double'),
 ('WT04', 'double'),
 ('WT05', 'double'),
 ('WT06', 'double'),
 ('WT07', 'double'),
 ('WT08', 'double'),
 ('WT09', 'double'),
 ('WESD', 'double'),
 ('WT10', 'double'),
 ('PSUN', 'double'),
 ('TSUN', 'double'),
 ('SN32', 'double'),
 ('SX32', 'double'),
 ('TOBS', 'double'),
 ('WT11', 'double')]

##Write raw loaded data files into Delta Tables - Bronze Layer

In a real world production environment, the multi-hop Delta Lake architecture would be achieved by writing the bronze, silver, and gold tables to established storage locations in cloud storage. For our purposes, we'll just write each layer of our architecture to seperate delta tables and identify them as bronze, silver, and gold.

In [0]:
#write raw dataframes to delta table 
airports.write.mode("overwrite").format("delta").saveAsTable("airport_data_bronze")
airport_weather.write.mode("overwrite").format("delta").saveAsTable("airport_weather_bronze")

##Silver Layer

To kick off our data cleansing and validation process, we'll first start off my reading in our bronze data tables into dataframes and then do a general check to see if duplicate rows exist in our raw dataframes.

In [0]:
# read in bronze tables 
airport_data_bronze = spark.read.table("airport_data_bronze")
airport_weather_bronze = spark.read.table("airport_weather_bronze")


In [0]:
''' Group the DataFrames by the columns in the tables and count the number of rows in each group. Then we'll filter the count generated 'count' column to include only rows with a count greater than 1 which indicates a duplicate row.'''

airport_duplicates = airport_data_bronze.groupby(airport_data_bronze.columns).count().filter(col("count") > 1)
airport_weather_duplicates = airport_weather_bronze.groupby(airport_weather_bronze.columns).count().filter(col("count") > 1)

airport_duplicates.show()
airport_weather_duplicates.show()

+-----------------+--------------------+----------------+----+-----+
|ORIGIN_AIRPORT_ID|DISPLAY_AIRPORT_NAME|ORIGIN_CITY_NAME|NAME|count|
+-----------------+--------------------+----------------+----+-----+
+-----------------+--------------------+----------------+----+-----+

+-------+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+-----+
|STATION|NAME|DATE|AWND|PGTM|PRCP|SNOW|SNWD|TAVG|TMAX|TMIN|WDF2|WDF5|WSF2|WSF5|WT01|WT02|WT03|WT04|WT05|WT06|WT07|WT08|WT09|WESD|WT10|PSUN|TSUN|SN32|SX32|TOBS|WT11|count|
+-------+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+-----+
+-------+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+-----+



Great! No duplicate rows exist in both the dataframe (don't get too used to this)

Now let's check for missing data in our tables. It's likely we'll have some missing data in our temperature and precipitation columns which we'll deal with later, for now let's ensure there's no missing data in the NAME and DATE columns.

In [0]:
airport_data_bronze.select([count(when(isnull(c), c)).alias(c) for c in airport_data_bronze.columns]).show()

airport_weather_bronze.select([count(when(isnull(c), c)).alias(c) for c in ['NAME', 'DATE']]).show()

+-----------------+--------------------+----------------+----+
|ORIGIN_AIRPORT_ID|DISPLAY_AIRPORT_NAME|ORIGIN_CITY_NAME|NAME|
+-----------------+--------------------+----------------+----+
|                0|                   0|               0|   0|
+-----------------+--------------------+----------------+----+

+----+----+
|NAME|DATE|
+----+----+
|   0|   0|
+----+----+



Now we'll perform a left join on the two dataframes so that all the data we have in the weather table that corresponds to the airports in the airports table gets connected to the airports table

In [0]:
joined_df = (airport_data_bronze
             .join(airport_weather_bronze, ['NAME'], "left_outer")
            )

In [0]:
joined_df.columns

Out[49]: ['NAME',
 'ORIGIN_AIRPORT_ID',
 'DISPLAY_AIRPORT_NAME',
 'ORIGIN_CITY_NAME',
 'STATION',
 'DATE',
 'AWND',
 'PGTM',
 'PRCP',
 'SNOW',
 'SNWD',
 'TAVG',
 'TMAX',
 'TMIN',
 'WDF2',
 'WDF5',
 'WSF2',
 'WSF5',
 'WT01',
 'WT02',
 'WT03',
 'WT04',
 'WT05',
 'WT06',
 'WT07',
 'WT08',
 'WT09',
 'WESD',
 'WT10',
 'PSUN',
 'TSUN',
 'SN32',
 'SX32',
 'TOBS',
 'WT11']

In [0]:
joined_df.select([count(when(isnull(c), c)).alias(c) for c in ['NAME',
 'ORIGIN_AIRPORT_ID',
 'DISPLAY_AIRPORT_NAME',
 'ORIGIN_CITY_NAME',
 'STATION',
 'DATE',
 'AWND',
 'PGTM',
 'PRCP',
 'SNOW',
 'SNWD',
 'TAVG',
 'TMAX',
 'TMIN']]).show()

+----+-----------------+--------------------+----------------+-------+----+----+-----+----+-----+-----+----+----+----+
|NAME|ORIGIN_AIRPORT_ID|DISPLAY_AIRPORT_NAME|ORIGIN_CITY_NAME|STATION|DATE|AWND| PGTM|PRCP| SNOW| SNWD|TAVG|TMAX|TMIN|
+----+-----------------+--------------------+----------------+-------+----+----+-----+----+-----+-----+----+----+----+
|   0|                0|                   0|               0|      1|   1|   9|31591|  22|11060|11565|7013|   6|   9|
+----+-----------------+--------------------+----------------+-------+----+----+-----+----+-----+-----+----+----+----+



In [0]:
airport_weather_bronze.select([count(when(isnull(c), c)).alias(c) for c in airport_weather.columns]).show()

+-------+----+----+----+-----+----+-----+-----+----+----+----+----+----+----+----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+
|STATION|NAME|DATE|AWND| PGTM|PRCP| SNOW| SNWD|TAVG|TMAX|TMIN|WDF2|WDF5|WSF2|WSF5| WT01| WT02| WT03| WT04| WT05| WT06| WT07| WT08| WT09| WESD| WT10| PSUN| TSUN| SN32| SX32| TOBS| WT11|
+-------+----+----+----+-----+----+-----+-----+----+----+----+----+----+----+----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+
|      0|   0|   0| 381|34737|  26|11768|12290|9933|  20|  21| 370| 481| 370| 481|24824|36865|33892|38409|38556|38269|38650|33950|38405|38669|38670|38336|38337|38310|38310|38320|38674|
+-------+----+----+----+-----+----+-----+-----+----+----+----+----+----+----+----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+-----+



We're good to go. Let's move on to performing some transformations to our data as well as some feature engineering

##Perform necessary transformations to delta tables and write to silver layer

Transformation objectives:
* Create a new "ORIGIN_STATE" column in the airports table that indicates the state the airport is located in
* Convert "DATE" column in the weather table to a date type 
* Create a new "MONTH" column in the weather table 
* The temperature columns in the weather table are currently in Fahrenheit, convert the "TAVG", "TMAX", and "TMIN" columns to Celsius and rename them to "TAVG_C", "TMAX_C", and "TMIN_C"
* The columns "PRCP", "SNOW", and "SNWD" are in inches, convert the measurements in these columns to mm and rename them to "PRCP_MM", "SNOW_MM", and "SNWD_MM"
* Drop uncessary columns in the weather table to only include the following columns in to new transformed table: 'NAME','DATE','AWND','PRCP_MM','SNOW_MM','SNWD_MM','TAVG_C', 'TMAX_C','TMIN_C'

In [0]:
# Create new State column in airports table 
# We'll do this by extracting the last two elements of the ORIGIN_CITY_NAME column
airports_silver = airport_data_bronze.withColumn("ORIGIN_STATE", col("ORIGIN_CITY_NAME").substr(-2,2))

In [0]:
display(airports_silver)

ORIGIN_AIRPORT_ID DISPLAY_AIRPORT_NAME ORIGIN_CITY_NAME NAME ORIGIN_STATE 12992 Adams Field Little Rock, AR NORTH LITTLE ROCK AIRPORT, AR US AR 10257 Albany International Albany, NY ALBANY INTERNATIONAL AIRPORT, NY US NY 10140 Albuquerque International Sunport Albuquerque, NM ALBUQUERQUE INTERNATIONAL AIRPORT, NM US NM 10299 Anchorage International Anchorage, AK ANCHORAGE TED STEVENS INTERNATIONAL AIRPORT, AK US AK 10397 Atlanta Municipal Atlanta, GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US GA 10423 Austin - Bergstrom International Austin, TX AUSTIN BERGSTROM INTERNATIONAL AIRPORT, TX US TX 10599 Birmingham Airport Birmingham, AL BIRMINGHAM AIRPORT, AL US AL 10529 Bradley International Hartford, CT HARTFORD BRADLEY INTERNATIONAL AIRPORT, CT US CT 10994 Charleston International Charleston, SC CHARLESTON INTL. AIRPORT, SC US SC 13232 Chicago Midway International Chicago, IL CHICAGO OHARE INTERNATIONAL AIRPORT, IL US IL 13930 Chicago O'Hare International Chicago, IL CHICAGO OHARE INTERNATIONAL AIRPORT, IL US IL 11193 Cincinnati/Northern Kentucky International Cincinnati, OH CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US OH 11042 Cleveland-Hopkins International Cleveland, OH CLEVELAND HOPKINS INTERNATIONAL AIRPORT, OH US OH 11298 Dallas Fort Worth Regional Dallas/Fort Worth, TX FORT WORTH MEACHAM FIELD, TX US TX 11259 Dallas Love Field Dallas, TX DALLAS FAA AIRPORT, TX US TX 11423 Des Moines Municipal Des Moines, IA DES MOINES INTERNATIONAL AIRPORT, IA US IA 11433 Detroit Metro Wayne County Detroit, MI DETROIT METRO AIRPORT, MI US MI 11057 Douglas Municipal Charlotte, NC CHARLOTTE DOUGLAS AIRPORT, NC US NC 11540 El Paso International El Paso, TX EL PASO INTERNATIONAL AIRPORT, TX US TX 13871 Eppley Airfield Omaha, NE GRAND ISLAND CENTRAL NE REGIONAL AIRPORT, NE US NE 11697 Fort Lauderdale-Hollywood International Fort Lauderdale, FL FORT LAUDERDALE INTERNATIONAL AIRPORT, FL US FL 11638 Fresno Air Terminal Fresno, CA FRESNO YOSEMITE INTERNATIONAL, CA US CA 10821 Friendship International Baltimore, MD BALTIMORE WASHINGTON INTERNATIONAL AIRPORT, MD US MD 13342 General Mitchell Field Milwaukee, WI MILWAUKEE MITCHELL AIRPORT, WI US WI 10792 Greater Buffalo International Buffalo, NY BUFFALO NIAGARA INTERNATIONAL, NY US NY 11996 Greenville-Spartanburg Greer, SC GREENVILLE DOWNTOWN AIRPORT, SC US SC 10800 Grenier Field/Manchester Municipal Manchester, NH MANCHESTER AIRPORT, NH US NH 12173 Hollywood-Burbank Midpoint Burbank, CA LOS ANGELES INTERNATIONAL AIRPORT, CA US CA 12266 Honolulu International Honolulu, HI HONOLULU INTERNATIONAL AIRPORT, HI US HI 12339 Indianapolis Muni/Weir Cook Indianapolis, IN INDIANAPOLIS INTERNATIONAL AIRPORT, IN US IN 12451 Jacksonville International Jacksonville, FL JACKSONVILLE INTERNATIONAL AIRPORT, FL US FL 11267 James M Cox/Dayton International Dayton, OH DAYTON WRIGHT BROTHERS AIRPORT, OH US OH 12478 John F. Kennedy International New York, NY LAGUARDIA AIRPORT, NY US NY 13830 Kahului Airport Kahului, HI HONOLULU INTERNATIONAL AIRPORT, HI US HI 13198 Kansas City International Kansas City, MO KANSAS CITY INTERNATIONAL AIRPORT, MO US MO 12758 Keahole Kona, HI KAILUA KONA KE AHOLE AIRPORT, HI US HI 11986 Kent County Grand Rapids, MI GRAND RAPIDS GERALD R FORD INTERNATIONAL AIRPORT, MI US MI 12953 LaGuardia New York, NY LAGUARDIA AIRPORT, NY US NY 15016 Lambert-St. Louis International St. Louis, MO ST LOUIS LAMBERT INTERNATIONAL AIRPORT, MO US MO 12982 Lihue Airport Lihue, HI LIHUE WEATHER SERVICE OFFICE AIRPORT 1020.1, HI US HI 10721 Logan International Boston, MA BOSTON, MA US MA 12954 Long Beach Daugherty Field Long Beach, CA LOS ANGELES INTERNATIONAL AIRPORT, CA US CA 12892 Los Angeles International Los Angeles, CA LOS ANGELES INTERNATIONAL AIRPORT, CA US CA 13495 Louis Armstrong New Orleans International New Orleans, LA NEW ORLEANS AIRPORT, LA US LA 12889 McCarran International Las Vegas, NV MCCARRAN INTERNATIONAL AIRPORT, NV US NV 15412 McGhee Tyson Knoxville, TN KNOXVILLE AIRPORT, TN US T

In [0]:
airports_silver.dtypes

Out[14]: [('ORIGIN_AIRPORT_ID', 'int'),
 ('DISPLAY_AIRPORT_NAME', 'string'),
 ('ORIGIN_CITY_NAME', 'string'),
 ('NAME', 'string'),
 ('ORIGIN_STATE', 'string')]

In [0]:
# The current format our dates are listed in the DATE column will not be accepted in the parsing function we're going to use to convert the column to date type, specifically for the current verion of Spark we're using (Spark 3.0). 
# The code below is a quick fix to alter the configuration and restore the behavior from before Spark 3.0, this allow the parsing to succeed
# NOTE: This is not best practice, but does not deviate from our intended objectives of this notebook: understanding multi-hop Delta Lake architecture
spark.conf.set("spark.sql.legacy.timeParserPolicy", "LEGACY")

# Let's start by defining function for the unit conversions

# F to C
def f_to_c(F):
    C = (F - 32) / 1.8
    C = round(C, 2)
    # C = format(C, '.2f')
    return C

# inches to mm
def in_to_mm(IN):
    mm = IN * 25.4
    mm = round(mm, 2)
    # mm = format(mm, '.2f')
    return mm

# F_to_C_UDF = udf(f_to_c)
# IN_to_MM_UDF = udf(in_to_mm)

# apply the unit conversions to the respective columns in the weather table and select a subset of columns for the final table
airport_weather_silver = (airport_weather_bronze
                            .withColumn("DATE", to_date(col("DATE"), "MM/dd/yyyy"))
                            .withColumn("MONTH", month(col('DATE')))
                            .withColumn('TAVG_C', f_to_c(col('TAVG')))
                            .withColumn('TMAX_C', f_to_c(col('TMAX')))
                            .withColumn('TMIN_C', f_to_c(col('TMIN')))
                            .withColumn('PRCP_MM', in_to_mm(col('PRCP')))
                            .withColumn('SNOW_MM', in_to_mm(col('SNOW')))
                            .withColumn('SNWD_MM', in_to_mm(col('SNWD')))
                         ).select( 'NAME','DATE','MONTH','AWND','PRCP_MM','SNOW_MM','SNWD_MM','TAVG_C', 'TMAX_C','TMIN_C')

In [0]:
display(airport_weather_silver)

NAME DATE MONTH AWND PRCP_MM SNOW_MM SNWD_MM TAVG_C TMAX_C TMIN_C ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-01 1 4.7 3.56 0.0 0.0 17.78 18.89 13.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-02 1 4.92 14.48 0.0 0.0 13.33 15.0 9.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-03 1 5.37 3.81 0.0 0.0 11.11 12.78 10.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-04 1 12.08 36.58 0.0 0.0 13.33 18.89 7.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-05 1 13.42 0.0 0.0 0.0 9.44 15.0 6.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-06 1 6.49 0.0 0.0 0.0 11.67 20.56 6.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-07 1 5.14 0.0 0.0 0.0 12.78 20.56 7.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-08 1 8.05 0.0 0.0 0.0 13.89 18.33 10.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-09 1 17.45 0.0 0.0 0.0 10.0 13.33 3.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-10 1 13.2 0.0 0.0 0.0 3.33 7.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-11 1 6.93 0.0 0.0 0.0 4.44 12.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-12 1 12.97 8.89 0.0 0.0 6.11 6.67 2.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-13 1 8.05 6.86 0.0 0.0 3.89 8.89 1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-14 1 11.63 0.0 0.0 0.0 7.22 8.33 3.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-15 1 10.74 0.0 0.0 0.0 4.44 7.78 0.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-16 1 7.61 0.0 0.0 0.0 3.33 11.67 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-17 1 4.03 2.54 0.0 0.0 5.56 10.0 1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-18 1 2.91 0.0 0.0 0.0 10.0 14.44 8.33 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-19 1 9.62 30.99 0.0 0.0 12.78 17.22 10.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-20 1 20.36 0.0 0.0 0.0 5.56 11.67 -1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-21 1 8.5 0.0 0.0 0.0 -0.56 6.67 -5.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-22 1 12.3 0.0 0.0 0.0 2.78 7.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-23 1 12.08 43.43 0.0 0.0 10.0 19.44 5.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-24 1 13.42 2.79 0.0 0.0 8.89 12.22 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-25 1 10.07 0.0 0.0 0.0 3.33 8.89 0.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-26 1 5.82 0.0 0.0 0.0 3.33 11.11 -2.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-27 1 2.01 0.0 0.0 0.0 5.56 10.56 0.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-28 1 6.26 0.0 0.0 0.0 7.22 15.0 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-29 1 12.53 4.32 0.0 0.0 7.22 10.56 -2.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-30 1 9.62 0.0 0.0 0.0 0.0 6.67 -4.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-31 1 2.91 0.0 0.0 0.0 2.78 11.67 -2.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-01 2 2.91 0.0 0.0 0.0 7.78 16.67 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-02 2 4.47 0.0 0.0 0.0 11.11 18.89 4.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-03 2 4.47 1.02 0.0 0.0 14.44 18.33 10.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-04 2 3.8 0.0 0.0 0.0 12.78 19.44 6.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-05 2 4.47 0.0 0.0 0.0 16.67 23.33 12.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-06 2 7.38 2.54 0.0 0.0 17.78 21.67 15.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-07 2 10.74 0.0 0.0 0.0 20.56 26.67 16.67 ATLANTA HARTSFIELD

Lets take a look at the dataypes of our columns after our transformation on the weather table

In [0]:
airport_weather_silver.dtypes

Out[19]: [('NAME', 'string'),
 ('DATE', 'date'),
 ('MONTH', 'int'),
 ('AWND', 'double'),
 ('PRCP_MM', 'double'),
 ('SNOW_MM', 'double'),
 ('SNWD_MM', 'double'),
 ('TAVG_C', 'double'),
 ('TMAX_C', 'double'),
 ('TMIN_C', 'double')]

Let's re-check for missing values in our transformed airport_weather_silver table, this time with including our new MONTH column in the check

In [0]:
# Count the number of null values in the NAME, DATE, and MONTH columnS
airport_weather_silver.select([count(when(isnull(c), c)).alias(c) for c in ['NAME', 'DATE', 'MONTH']]).show()

# Count the number of null or NaN values in each column
# airport_weather_silver.select([count(when(isnull(c) | isnan(c), c)).alias(c) for c in airport_weather_silver.columns]).show()


+----+-----+-----+
|NAME| DATE|MONTH|
+----+-----+-----+
|   0|22252|22252|
+----+-----+-----+



Looks like we now have some null values in our transformed dataframe. Let's inspect the dataframe to see why that may have happened.

In [0]:

display(airport_weather_silver.filter(isnull("DATE")).sample(0.2))

NAME DATE MONTH AWND PRCP_MM SNOW_MM SNWD_MM TAVG_C TMAX_C TMIN_C ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.25 0.0 null null null -6.67 -23.89 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 3.8 0.0 null null null 5.56 -14.44 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.93 0.0 null null null 3.33 -12.22 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.14 0.0 null null null 6.11 -10.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.04 0.0 null null null 5.0 -14.44 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.82 3.3 null null null 6.67 -5.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 8.28 0.0 null null null 3.89 -15.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.16 1.27 null null null 4.44 -6.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.47 0.25 null null null -5.56 -18.33 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.92 0.0 null null null 7.78 -11.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.47 0.0 null null null 4.44 -13.89 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.7 17.27 null null null 3.89 -3.89 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.26 0.51 null null null 0.56 -6.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.47 0.25 null null null -1.67 -11.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.59 0.0 null null null 7.78 -10.0 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.26 0.0 null null null 10.0 -6.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 0.0 null null null 5.56 -8.33 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.14 0.0 null null null 12.78 -1.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.26 0.0 null null null 13.33 -1.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 9.17 0.25 null null null 1.67 -6.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.82 18.8 null null null 10.56 0.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.16 0.0 null null null 18.89 1.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.25 11.43 null null null 5.56 0.0 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 0.0 null null null 19.44 -1.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 2.91 0.51 null null null 6.67 -2.78 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 0.0 null null null 22.78 2.22 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 8.72 0.0 null null null 21.67 3.33 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.16 0.0 null null null 22.78 7.22 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 0.0 null null null 21.11 1.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.26 0.0 null null null 25.0 3.89 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.38 0.0 null null null 27.22 5.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 0.0 null null null 30.56 6.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.49 0.0 null null null 29.44 11.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.59 2.79 null null null 25.56 11.67 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.14 0.0 null null null 26.67 11.11 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.16 0.0 null null null 30.0 8.33 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 4.7 0.0 null null null 27.78 7.78 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 5.59 0.0 null null null 24.44 10.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.71 10.67 null null null 28.33 13.33 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.38 0.51 null null null 27.78 10.56 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.16 0.0 null null null 27.22 7.22 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 6.49 0.0 null null null 28.33 7.22 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 7.61 0.0 null null null 28.89 7.78 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US null null 9.62 0.0 null null null 27.78 8.33 ASPEN PITKIN CO AIRPORT SARDY FIE

It seems there's a subset of aiports for which the data type conversion for the date column didn't work as intended. Let's collect those airports into a list and use it to verify what the original date column looked like for those airports

In [0]:
# Create a single column dataframe with the distinct airport names that have a null date 
null_dates_df = airport_weather_silver.filter(isnull("DATE"))
column_values = null_dates_df.select("NAME").distinct()

# Collect airport names into a list
null_date_airports = column_values.rdd.map(lambda x: x.NAME).collect()
print(null_date_airports)
# display(column_values)


['GREENSBORO AIRPORT, NC US', 'BIRMINGHAM AIRPORT, AL US', 'WICHITA COLONEL JAMES JABARA AIRPORT, KS US', 'ANCHORAGE TED STEVENS INTERNATIONAL AIRPORT, AK US', 'GREENVILLE DOWNTOWN AIRPORT, SC US', 'FAYETTEVILLE SPRINGDALE NW AR REGL AIRPORT, AR US', 'WILMINGTON INTERNATIONAL AIRPORT, NC US', 'EL PASO INTERNATIONAL AIRPORT, TX US', 'LOUISVILLE INTERNATIONAL AIRPORT, KY US', 'ALBUQUERQUE INTERNATIONAL AIRPORT, NM US', 'ASHEVILLE AIRPORT, NC US', 'ALBANY INTERNATIONAL AIRPORT, NY US', 'HARTFORD BRADLEY INTERNATIONAL AIRPORT, CT US', 'SAN JUAN L M MARIN INTERNATIONAL AIRPORT, PR US', 'HOUSTON WILLIAM P HOBBY AIRPORT, TX US', 'ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US', 'LIHUE WEATHER SERVICE OFFICE AIRPORT 1020.1, HI US', 'LEXINGTON BLUEGRASS AIRPORT, KY US', 'KNOXVILLE AIRPORT, TN US', 'FRESNO YOSEMITE INTERNATIONAL, CA US', 'SAVANNAH INTERNATIONAL AIRPORT, GA US', 'GRAND RAPIDS GERALD R FORD INTERNATIONAL AIRPORT, MI US', 'DAYTON WRIGHT BROTHERS AIRPORT, OH US', 'JACKSON INTERNATIONAL 

We already know for a fact there weren't any null values in the date column in the original data. Let's check what the date values were for these airports by filtering the bronze layer of our airport weather table to only include the airports we've collected in null_dates_airports.

In [0]:
# display filtered airport_weather_bronze dataframe
display(airport_weather_bronze.filter(col("NAME").isin(null_date_airports)).sample(0.2))

STATION NAME DATE AWND PGTM PRCP SNOW SNWD TAVG TMAX TMIN WDF2 WDF5 WSF2 WSF5 WT01 WT02 WT03 WT04 WT05 WT06 WT07 WT08 WT09 WESD WT10 PSUN TSUN SN32 SX32 TOBS WT11 USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-01 3.13 null 0.0 null null null 17.0 -8.0 320.0 300.0 8.1 13.0 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-04 4.92 null 0.0 null null null 37.0 6.0 170.0 170.0 12.1 14.1 null null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-05 3.8 null 0.0 null null null 42.0 6.0 190.0 310.0 8.9 13.0 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-11 4.25 null 0.17 null null null 31.0 25.0 10.0 10.0 12.1 17.0 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-12 3.8 null 0.0 null null null 32.0 11.0 210.0 350.0 8.1 10.1 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-16 3.8 null 0.16 null null null 34.0 22.0 350.0 360.0 12.1 16.1 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-21 5.14 null 0.25 null null null 40.0 20.0 190.0 180.0 21.0 29.1 1.0 1.0 null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-27 4.25 null 0.0 null null null 35.0 6.0 190.0 150.0 13.0 17.0 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-01-31 6.26 null 0.0 null null null 38.0 2.0 220.0 220.0 15.0 16.1 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-01 6.04 null 0.0 null null null 41.0 6.0 200.0 210.0 10.1 13.0 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-06 6.71 null 0.11 null null null 32.0 10.0 340.0 330.0 17.0 23.9 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-12 4.92 null 0.0 null null null 35.0 0.0 210.0 230.0 13.0 16.1 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-19 4.47 null 0.03 null null null 20.0 10.0 330.0 320.0 14.1 19.9 1.0 null null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-21 10.51 null 0.0 null null null 31.0 3.0 170.0 180.0 28.0 42.1 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-23 6.93 null 0.03 null null null 25.0 10.0 320.0 330.0 16.1 23.0 1.0 null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-02-26 4.92 null 0.0 null null null 46.0 12.0 180.0 280.0 13.0 18.1 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-03-03 3.8 null 0.28 null null null 33.0 26.0 320.0 310.0 14.1 21.9 1.0 1.0 null null null null null 1.0 null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US 2019-03-15 4.92 null 0.0 null null null 35.0 1.0 220.0 200.0 13.0 17.0 null null null null null null null null null null null null null null null null null USW00093073 ASPEN PITKIN CO AIRPORT SARDY FIELD, C

Looks like we have dates in two different formats in our raw data which is causing issues when converting the column to date type. Iinitally we had thought the format was MM/dd/YYY, but as we can see a subset of airports have the date format as YYYY-MM-dd.

We'll have to convert the data type for the DATE column in our silver layer conditionally based on the format the original data is in.

Let's re-run our transformation cell, but this time we'll add a conditional transformation for the DATE column. The conditional statement will change the data type of the DATE column differently depending on whether the airport NAME is part of the group of airport that have the original date format as YYYY-MM-dd.

In [0]:
# The current format our dates are listed in the DATE column will not be accepted in the parsing function we're going to use to convert the column to date type, specifically for the current verion of Spark we're using (Spark 3.0). 
# The code below is a quick fix to alter the configuration and restore the behavior from before Spark 3.0, this allow the parsing to succeed
# NOTE: This is not best practice, but does not deviate from our intended objectives of this notebook: understanding multi-hop Delta Lake architecture
spark.conf.set("spark.sql.legacy.timeParserPolicy", "LEGACY")

# Let's start by defining function for the unit conversions

# F to C
def f_to_c(F):
    C = (F - 32) / 1.8
    C = round(C, 2)
    # C = format(C, '.2f')
    return C

# inches to mm
def in_to_mm(IN):
    mm = IN * 25.4
    mm = round(mm, 2)
    # mm = format(mm, '.2f')
    return mm

# F_to_C_UDF = udf(f_to_c)
# IN_to_MM_UDF = udf(in_to_mm)

# apply the unit conversions to the respective columns in the weather table and select a subset of columns for the final table
airport_weather_silver = (airport_weather
                            .withColumn("DATE", 
                                        when(col("NAME").isin(null_date_airports), to_date(col("DATE"), "yyyy-MM-dd"))
                                        .otherwise(to_date(col("DATE"), "MM/dd/yyyy")))
                            .withColumn("MONTH", month(col('DATE')))
                            .withColumn('TAVG_C', f_to_c(col('TAVG')))
                            .withColumn('TMAX_C', f_to_c(col('TMAX')))
                            .withColumn('TMIN_C', f_to_c(col('TMIN')))
                            .withColumn('PRCP_MM', in_to_mm(col('PRCP')))
                            .withColumn('SNOW_MM', in_to_mm(col('SNOW')))
                            .withColumn('SNWD_MM', in_to_mm(col('SNWD')))
                         ).select( 'NAME','DATE','MONTH','AWND','PRCP_MM','SNOW_MM','SNWD_MM','TAVG_C', 'TMAX_C','TMIN_C')

In [0]:
# Check data types
display(airport_weather_silver.dtypes)

_1 _2 NAME string DATE date MONTH int AWND double PRCP_MM double SNOW_MM double SNWD_MM double TAVG_C double TMAX_C double TMIN_C double

In [0]:
# Check for null values
airport_weather_silver.select([count(when(isnull(c), c)).alias(c) for c in ['NAME', 'DATE', 'MONTH']]).show()

+----+----+-----+
|NAME|DATE|MONTH|
+----+----+-----+
|   0|   0|    0|
+----+----+-----+



Problem solved!

Now let's check the remaining columns in the airport_weather_silver dataframe for missing values

In [0]:
# Count the number of null or NaN values in each column
airport_weather_silver.select([count(when(isnull(c), c)).alias(c) for c in ['AWND','PRCP_MM','SNOW_MM','SNWD_MM','TAVG_C', 'TMAX_C','TMIN_C']]).show()

+----+-------+-------+-------+------+------+------+
|AWND|PRCP_MM|SNOW_MM|SNWD_MM|TAVG_C|TMAX_C|TMIN_C|
+----+-------+-------+-------+------+------+------+
| 381|     26|  11768|  12290|  9933|    20|    21|
+----+-------+-------+-------+------+------+------+



As expected, we have a lot of missing weather data. 

There are multiple ways of addressing missing data in big data projects, some of which are:
- Deleting rows with missing values
- Replacing missing values with a constant 
- Predicting missing values 

We'll use some of these methods to address the missing values in our columns

The quantity of missing data for columns TMAX_C, TMIN_C, and PRCP_MM is insignificant so let's go ahead and drop the rows with missing data for these columns.

In [0]:
# drop rows with null values in columns "PRCP_MM", "TMAX_C", and "TMIN_C"
airport_weather_silver_2 = airport_weather_silver.na.drop(subset=["PRCP_MM", "TMAX_C", "TMIN_C"])
airport_weather_silver_2.select([count(when(isnull(c), c)).alias(c) for c in ['AWND','PRCP_MM','SNOW_MM','SNWD_MM','TAVG_C', 'TMAX_C','TMIN_C']]).show()

+----+-------+-------+-------+------+------+------+
|AWND|PRCP_MM|SNOW_MM|SNWD_MM|TAVG_C|TMAX_C|TMIN_C|
+----+-------+-------+-------+------+------+------+
| 367|      0|  11736|  12264|  9895|     0|     0|
+----+-------+-------+-------+------+------+------+



Now in order to resolve the missing values in the AWND column, we're going to replace the missing values in that column with the average max wind speed aggregated based on the city and month. Let's start by first joining our weather dataframe with our airports dataframe so that we have access to the city column in the airports dataframe.

In [0]:
joined_df = (airport_weather_silver_2
             .join(airports_silver, ['NAME'], "left_outer")
            )

In [0]:
display(airport_weather_silver_2)

NAME DATE MONTH AWND PRCP_MM SNOW_MM SNWD_MM TAVG_C TMAX_C TMIN_C ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-01 1 4.7 3.56 0.0 0.0 17.78 18.89 13.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-02 1 4.92 14.48 0.0 0.0 13.33 15.0 9.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-03 1 5.37 3.81 0.0 0.0 11.11 12.78 10.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-04 1 12.08 36.58 0.0 0.0 13.33 18.89 7.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-05 1 13.42 0.0 0.0 0.0 9.44 15.0 6.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-06 1 6.49 0.0 0.0 0.0 11.67 20.56 6.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-07 1 5.14 0.0 0.0 0.0 12.78 20.56 7.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-08 1 8.05 0.0 0.0 0.0 13.89 18.33 10.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-09 1 17.45 0.0 0.0 0.0 10.0 13.33 3.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-10 1 13.2 0.0 0.0 0.0 3.33 7.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-11 1 6.93 0.0 0.0 0.0 4.44 12.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-12 1 12.97 8.89 0.0 0.0 6.11 6.67 2.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-13 1 8.05 6.86 0.0 0.0 3.89 8.89 1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-14 1 11.63 0.0 0.0 0.0 7.22 8.33 3.89 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-15 1 10.74 0.0 0.0 0.0 4.44 7.78 0.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-16 1 7.61 0.0 0.0 0.0 3.33 11.67 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-17 1 4.03 2.54 0.0 0.0 5.56 10.0 1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-18 1 2.91 0.0 0.0 0.0 10.0 14.44 8.33 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-19 1 9.62 30.99 0.0 0.0 12.78 17.22 10.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-20 1 20.36 0.0 0.0 0.0 5.56 11.67 -1.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-21 1 8.5 0.0 0.0 0.0 -0.56 6.67 -5.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-22 1 12.3 0.0 0.0 0.0 2.78 7.22 -1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-23 1 12.08 43.43 0.0 0.0 10.0 19.44 5.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-24 1 13.42 2.79 0.0 0.0 8.89 12.22 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-25 1 10.07 0.0 0.0 0.0 3.33 8.89 0.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-26 1 5.82 0.0 0.0 0.0 3.33 11.11 -2.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-27 1 2.01 0.0 0.0 0.0 5.56 10.56 0.56 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-28 1 6.26 0.0 0.0 0.0 7.22 15.0 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-29 1 12.53 4.32 0.0 0.0 7.22 10.56 -2.22 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-30 1 9.62 0.0 0.0 0.0 0.0 6.67 -4.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-31 1 2.91 0.0 0.0 0.0 2.78 11.67 -2.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-01 2 2.91 0.0 0.0 0.0 7.78 16.67 1.11 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-02 2 4.47 0.0 0.0 0.0 11.11 18.89 4.44 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-03 2 4.47 1.02 0.0 0.0 14.44 18.33 10.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-04 2 3.8 0.0 0.0 0.0 12.78 19.44 6.67 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-05 2 4.47 0.0 0.0 0.0 16.67 23.33 12.78 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-06 2 7.38 2.54 0.0 0.0 17.78 21.67 15.0 ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-02-07 2 10.74 0.0 0.0 0.0 20.56 26.67 16.67 ATLANTA HARTSFIELD

In [0]:
display(joined_df)

NAME DATE MONTH AWND PRCP_MM SNOW_MM SNWD_MM TAVG_C TMAX_C TMIN_C ORIGIN_AIRPORT_ID DISPLAY_AIRPORT_NAME ORIGIN_CITY_NAME ORIGIN_STATE ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-01 1 4.7 3.56 0.0 0.0 17.78 18.89 13.89 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-02 1 4.92 14.48 0.0 0.0 13.33 15.0 9.44 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-03 1 5.37 3.81 0.0 0.0 11.11 12.78 10.56 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-04 1 12.08 36.58 0.0 0.0 13.33 18.89 7.22 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-05 1 13.42 0.0 0.0 0.0 9.44 15.0 6.67 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-06 1 6.49 0.0 0.0 0.0 11.67 20.56 6.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-07 1 5.14 0.0 0.0 0.0 12.78 20.56 7.22 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-08 1 8.05 0.0 0.0 0.0 13.89 18.33 10.0 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-09 1 17.45 0.0 0.0 0.0 10.0 13.33 3.89 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-10 1 13.2 0.0 0.0 0.0 3.33 7.22 -1.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-11 1 6.93 0.0 0.0 0.0 4.44 12.22 -1.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-12 1 12.97 8.89 0.0 0.0 6.11 6.67 2.78 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-13 1 8.05 6.86 0.0 0.0 3.89 8.89 1.67 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-14 1 11.63 0.0 0.0 0.0 7.22 8.33 3.89 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-15 1 10.74 0.0 0.0 0.0 4.44 7.78 0.0 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-16 1 7.61 0.0 0.0 0.0 3.33 11.67 -1.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-17 1 4.03 2.54 0.0 0.0 5.56 10.0 1.67 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-18 1 2.91 0.0 0.0 0.0 10.0 14.44 8.33 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-19 1 9.62 30.99 0.0 0.0 12.78 17.22 10.56 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-20 1 20.36 0.0 0.0 0.0 5.56 11.67 -1.67 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-21 1 8.5 0.0 0.0 0.0 -0.56 6.67 -5.56 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-22 1 12.3 0.0 0.0 0.0 2.78 7.22 -1.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-23 1 12.08 43.43 0.0 0.0 10.0 19.44 5.56 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-24 1 13.42 2.79 0.0 0.0 8.89 12.22 1.11 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-25 1 10.07 0.0 0.0 0.0 3.33 8.89 0.0 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-26 1 5.82 0.0 0.0 0.0 3.33 11.11 -2.22 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US 2019-01-27 1 2.01 0.0 0.0 0.0 5.56 10.56 0.56 10397 Atlanta Municipal Atlanta, GA GA ATLANTA HARTSFIELD JACKSON INT

In [0]:
joined_df.select([count(when(isnull(c), c)).alias(c) for c in joined_df.columns]).show()

+----+----+-----+----+-------+-------+-------+------+------+------+-----------------+--------------------+----------------+------------+
|NAME|DATE|MONTH|AWND|PRCP_MM|SNOW_MM|SNWD_MM|TAVG_C|TMAX_C|TMIN_C|ORIGIN_AIRPORT_ID|DISPLAY_AIRPORT_NAME|ORIGIN_CITY_NAME|ORIGIN_STATE|
+----+----+-----+----+-------+-------+-------+------+------+------+-----------------+--------------------+----------------+------------+
|   0|   0|    0| 367|      0|  14195|  14723| 10254|     0|     0|             7639|                7639|            7639|        7639|
+----+----+-----+----+-------+-------+-------+------+------+------+-----------------+--------------------+----------------+------------+



In [0]:
display(airport_weather_silver_2.select('NAME').distinct())

NAME GREENSBORO AIRPORT, NC US BIRMINGHAM AIRPORT, AL US SEATTLE TACOMA AIRPORT, WA US AUSTIN BERGSTROM INTERNATIONAL AIRPORT, TX US MINNEAPOLIS ST. PAUL INTERNATIONAL AIRPORT, MN US WICHITA COLONEL JAMES JABARA AIRPORT, KS US PITTSBURGH ALLEGHENY CO AIRPORT, PA US NASHVILLE INTERNATIONAL AIRPORT, TN US SAN JOSE INTERNATIONAL AIRPORT, CA US ANCHORAGE TED STEVENS INTERNATIONAL AIRPORT, AK US HONOLULU INTERNATIONAL AIRPORT, HI US LAGUARDIA AIRPORT, NY US GREENVILLE DOWNTOWN AIRPORT, SC US MIAMI INTERNATIONAL AIRPORT, FL US FAYETTEVILLE SPRINGDALE NW AR REGL AIRPORT, AR US WILMINGTON INTERNATIONAL AIRPORT, NC US EL PASO INTERNATIONAL AIRPORT, TX US SAN FRANCISCO INTERNATIONAL AIRPORT, CA US LOUISVILLE INTERNATIONAL AIRPORT, KY US ALBUQUERQUE INTERNATIONAL AIRPORT, NM US NEW ORLEANS AIRPORT, LA US RALEIGH AIRPORT, NC US ASHEVILLE AIRPORT, NC US ALBANY INTERNATIONAL AIRPORT, NY US HARTFORD BRADLEY INTERNATIONAL AIRPORT, CT US ST LOUIS LAMBERT INTERNATIONAL AIRPORT, MO US KANSAS CITY INTERNATIONAL AIRPORT, MO US DENVER INTERNATIONAL AIRPORT, CO US SAN JUAN L M MARIN INTERNATIONAL AIRPORT, PR US MCCARRAN INTERNATIONAL AIRPORT, NV US HOUSTON WILLIAM P HOBBY AIRPORT, TX US ASPEN PITKIN CO AIRPORT SARDY FIELD, CO US TAMPA INTERNATIONAL AIRPORT, FL US LIHUE WEATHER SERVICE OFFICE AIRPORT 1020.1, HI US LEXINGTON BLUEGRASS AIRPORT, KY US KNOXVILLE AIRPORT, TN US DALLAS FAA AIRPORT, TX US FORT WORTH MEACHAM FIELD, TX US FRESNO YOSEMITE INTERNATIONAL, CA US SAVANNAH INTERNATIONAL AIRPORT, GA US CHARLOTTE DOUGLAS AIRPORT, NC US SALT LAKE CITY INTERNATIONAL AIRPORT, UT US GRAND RAPIDS GERALD R FORD INTERNATIONAL AIRPORT, MI US FORT MYERS SW FLORIDA REGIONAL AIRPORT, FL US BALTIMORE WASHINGTON INTERNATIONAL AIRPORT, MD US DAYTON WRIGHT BROTHERS AIRPORT, OH US COLUMBUS OHIO STATE UNIVERSITY AIRPORT, OH US ORLANDO INTERNATIONAL AIRPORT, FL US PHILADELPHIA INTERNATIONAL AIRPORT, PA US PHOENIX AIRPORT, AZ US FORT LAUDERDALE INTERNATIONAL AIRPORT, FL US LOS ANGELES INTERNATIONAL AIRPORT, CA US PORTLAND INTERNATIONAL AIRPORT, OR US JACKSON INTERNATIONAL AIRPORT, MS US WEST PALM BEACH INTERNATIONAL AIRPORT, FL US CEDAR RAPIDS MUNICIPAL AIRPORT, IA US COLORADO SPRINGS MUNICIPAL AIRPORT, CO US HUNTSVILLE INTNL AIRPORT, AL US ROCHESTER GREATER INTERNATIONAL, NY US BUFFALO JOHNSON CO AIRPORT, WY US SANTA ANA JOHN WAYNE AIRPORT, CA US BUFFALO NIAGARA INTERNATIONAL, NY US SAN DIEGO INTERNATIONAL AIRPORT, CA US CHATTANOOGA AIRPORT, TN US CHARLESTON INTL. AIRPORT, SC US BOSTON, MA US HOUSTON INTERCONTINENTAL AIRPORT, TX US SACRAMENTO METROPOLITAN AIRPORT, CA US WASHINGTON DULLES INTERNATIONAL AIRPORT, VA US BOZEMAN GALLATIN FIELD AIRPORT, MT US DETROIT METRO AIRPORT, MI US BURLINGTON INTERNATIONAL AIRPORT, VT US BATON ROUGE METRO AIRPORT, LA US CLEVELAND HOPKINS INTERNATIONAL AIRPORT, OH US NORTH LITTLE ROCK AIRPORT, AR US CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US CHICAGO OHARE INTERNATIONAL AIRPORT, IL US SAN ANTONIO INTERNATIONAL AIRPORT, TX US DES MOINES INTERNATIONAL AIRPORT, IA US ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US NEWARK LIBERTY INTERNATIONAL AIRPORT, NJ US BOISE AIR TERMINAL, ID US JACKSONVILLE INTERNATIONAL AIRPORT, FL US KAILUA KONA KE AHOLE AIRPORT, HI US INDIANAPOLIS INTERNATIONAL AIRPORT, IN US SPOKANE INTERNATIONAL AIRPORT, WA US TRAVERSE CITY CHERRY CAPITAL AIRPORT, MI US OKLAHOMA CITY WILL ROGERS WORLD AIRPORT, OK US NORFOLK INTERNATIONAL AIRPORT, VA US MILWAUKEE MITCHELL AIRPORT, WI US TALLAHASSEE REGIONAL AIRPORT, FL US PORT ARTHUR SE TX REGIONAL AIRPORT, TX US MEMPHIS INTERNATIONAL AIRPORT, TN US TALLAHASSEE AIRPORT, FL US DESERT RESORTS REGIONAL AIRPORT, CA US MADISON DANE CO REGIONAL AIRPORT, WI US RENO AIRPORT, NV US NORTH MYRTLE BEACH, SC US SYRACUSE HANCOCK INTERNATIONAL AIRPORT, NY US PORTLAND JETPORT, ME US SPRINGFIELD WEATHER SERVICE OFFICE AIRPORT, MO US MANCHESTER AIRPORT, NH US NEWPORT STATE AIRPORT, RI US RAPID CITY REGIONAL AIRPORT, SD US GRAND ISLAND CENTRAL NE REGIONAL AIRPORT, NE US RICHMOND INTERN

In [0]:
display(airports_silver.select('NAME').distinct())

NAME GREENSBORO AIRPORT, NC US BIRMINGHAM AIRPORT, AL US SEATTLE TACOMA AIRPORT, WA US AUSTIN BERGSTROM INTERNATIONAL AIRPORT, TX US MINNEAPOLIS ST. PAUL INTERNATIONAL AIRPORT, MN US PITTSBURGH ALLEGHENY CO AIRPORT, PA US SPOKANE INTERNATIONAL AIRPORT, WA US SAN JOSE INTERNATIONAL AIRPORT, CA US ANCHORAGE TED STEVENS INTERNATIONAL AIRPORT, AK US HONOLULU INTERNATIONAL AIRPORT, HI US GREENVILLE DOWNTOWN AIRPORT, SC US LAGUARDIA AIRPORT, NY US MIAMI INTERNATIONAL AIRPORT, FL US FAYETTEVILLE SPRINGDALE NW AR REGL AIRPORT, AR US OKLAHOMA CITY WILL ROGERS WORLD AIRPORT, OK US EL PASO INTERNATIONAL AIRPORT, TX US SAN FRANCISCO INTERNATIONAL AIRPORT, CA US LOUISVILLE INTERNATIONAL AIRPORT, KY US ALBUQUERQUE INTERNATIONAL AIRPORT, NM US NORFOLK INTERNATIONAL AIRPORT, VA US NEW ORLEANS AIRPORT, LA US RALEIGH AIRPORT, NC US ALBANY INTERNATIONAL AIRPORT, NY US HARTFORD BRADLEY INTERNATIONAL AIRPORT, CT US ST LOUIS LAMBERT INTERNATIONAL AIRPORT, MO US KANSAS CITY INTERNATIONAL AIRPORT, MO US MILWAUKEE MITCHELL AIRPORT, WI US DENVER INTERNATIONAL AIRPORT, CO US MCCARRAN INTERNATIONAL AIRPORT, NV US HOUSTON WILLIAM P HOBBY AIRPORT, TX US TAMPA INTERNATIONAL AIRPORT, FL US LIHUE WEATHER SERVICE OFFICE AIRPORT 1020.1, HI US TALLAHASSEE REGIONAL AIRPORT, FL US KNOXVILLE AIRPORT, TN US FORT WORTH MEACHAM FIELD, TX US DALLAS FAA AIRPORT, TX US FRESNO YOSEMITE INTERNATIONAL, CA US SAVANNAH INTERNATIONAL AIRPORT, GA US PORT ARTHUR SE TX REGIONAL AIRPORT, TX US CHARLOTTE DOUGLAS AIRPORT, NC US GRAND RAPIDS GERALD R FORD INTERNATIONAL AIRPORT, MI US SALT LAKE CITY INTERNATIONAL AIRPORT, UT US FORT MYERS SW FLORIDA REGIONAL AIRPORT, FL US MEMPHIS INTERNATIONAL AIRPORT, TN US BALTIMORE WASHINGTON INTERNATIONAL AIRPORT, MD US DESERT RESORTS REGIONAL AIRPORT, CA US DAYTON WRIGHT BROTHERS AIRPORT, OH US COLUMBUS OHIO STATE UNIVERSITY AIRPORT, OH US ORLANDO INTERNATIONAL AIRPORT, FL US PHILADELPHIA INTERNATIONAL AIRPORT, PA US PHOENIX AIRPORT, AZ US FORT LAUDERDALE INTERNATIONAL AIRPORT, FL US MADISON DANE CO REGIONAL AIRPORT, WI US LOS ANGELES INTERNATIONAL AIRPORT, CA US WEST PALM BEACH INTERNATIONAL AIRPORT, FL US PORTLAND INTERNATIONAL AIRPORT, OR US NORTH MYRTLE BEACH, SC US RENO AIRPORT, NV US ROCHESTER GREATER INTERNATIONAL, NY US SANTA ANA JOHN WAYNE AIRPORT, CA US SYRACUSE HANCOCK INTERNATIONAL AIRPORT, NY US BUFFALO NIAGARA INTERNATIONAL, NY US SAN DIEGO INTERNATIONAL AIRPORT, CA US PORTLAND JETPORT, ME US CHARLESTON INTL. AIRPORT, SC US BOSTON, MA US MANCHESTER AIRPORT, NH US NEWPORT STATE AIRPORT, RI US SACRAMENTO METROPOLITAN AIRPORT, CA US WASHINGTON DULLES INTERNATIONAL AIRPORT, VA US DETROIT METRO AIRPORT, MI US CLEVELAND HOPKINS INTERNATIONAL AIRPORT, OH US NORTH LITTLE ROCK AIRPORT, AR US CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US CHICAGO OHARE INTERNATIONAL AIRPORT, IL US SAN ANTONIO INTERNATIONAL AIRPORT, TX US DES MOINES INTERNATIONAL AIRPORT, IA US GRAND ISLAND CENTRAL NE REGIONAL AIRPORT, NE US ATLANTA HARTSFIELD JACKSON INTERNATIONAL AIRPORT, GA US RICHMOND INTERNATIONAL AIRPORT, VA US NEWARK LIBERTY INTERNATIONAL AIRPORT, NJ US SAN JUAN L M MARIN INTERNATIONAL AIRPORT, US BOISE AIR TERMINAL, ID US JACKSONVILLE INTERNATIONAL AIRPORT, FL US KAILUA KONA KE AHOLE AIRPORT, HI US INDIANAPOLIS INTERNATIONAL AIRPORT, IN US

In [0]:

# display(airport_weather_silver_2.filter(isnull("SNOW_MM") | isnull("SNWD_MM")).sample(0.2))

display(airport_weather_silver_2.filter(isnull("TAVG_C")))

NAME DATE MONTH AWND PRCP_MM SNOW_MM SNWD_MM TAVG_C TMAX_C TMIN_C CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-01 1 5.82 0.0 null null null 11.67 5.0 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-02 1 5.82 0.0 null null null 6.67 3.89 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-03 1 3.8 0.0 null null null 6.11 -0.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-04 1 5.82 6.6 null null null 11.67 -1.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-05 1 6.93 0.0 null null null 11.11 1.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-06 1 3.8 0.0 null null null 11.67 -1.11 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-07 1 10.07 0.0 null null null 16.11 6.11 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-08 1 15.43 0.0 null null null 18.33 5.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-09 1 12.75 0.0 null null null 6.11 -5.0 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-10 1 6.71 0.0 null null null -1.67 -5.0 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-11 1 4.47 0.0 null null null 1.67 -2.78 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-12 1 4.7 7.87 null null null 1.11 -1.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-13 1 8.05 8.64 null null null 1.11 -1.11 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-14 1 3.58 0.0 null null null 0.0 -7.78 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-15 1 5.37 0.0 null null null 0.56 -9.44 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-16 1 4.25 0.25 null null null 2.22 0.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-17 1 2.24 4.06 null null null 5.0 0.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-18 1 5.14 0.0 null null null 3.89 1.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-19 1 10.51 26.42 null null null 5.0 -5.0 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-20 1 12.53 1.02 null null null -5.0 -11.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-21 1 5.14 0.0 null null null -7.22 -17.22 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-22 1 7.38 0.0 null null null 6.67 -10.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-23 1 9.62 20.57 null null null 11.11 0.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-24 1 11.41 0.76 null null null 0.56 -3.33 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-25 1 10.96 0.0 null null null -2.22 -10.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-26 1 10.74 0.0 null null null 3.89 -4.44 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-27 1 9.62 0.0 null null null 3.89 -6.11 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-28 1 10.07 1.52 null null null 10.0 -5.56 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-29 1 14.32 0.0 null null null -3.89 -8.33 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-30 1 12.75 0.0 null null null -8.33 -18.33 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-01-31 1 5.37 0.0 null null null -7.78 -18.89 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-01 2 3.13 0.25 null null null -0.56 -8.33 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-02 2 2.68 0.0 null null null 8.33 -6.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-03 2 2.68 0.0 null null null 18.89 -1.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-04 2 5.37 1.27 null null null 16.67 -1.11 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-05 2 5.14 1.52 null null null 13.33 6.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-06 2 2.24 40.89 null null null 16.67 6.67 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-07 2 7.38 29.21 null null null 18.89 3.89 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-08 2 13.87 0.0 null null null 3.89 -7.22 CINCINNATI MUNICIPAL AIRPORT LUNKEN FIELD, OH US 2019-02-09 2 7.38 0.0 null null null 0.0 -9.44 CINCINNATI MUNICIPAL A

Now let's examine the null values in the SNOW_MM and SNWD_MM columns

In [0]:
#join two dataframe
airport_weather_silver = airport_weather_silver.withColumnRenamed('NAME','NAME_DROP')

# joined_df = (airports_silver
#              .join(airport_weather_silver, airports_silver.NAME == airport_weather_silver.NAME_DROP, 'left')
#             )


# display(joined_df)

# Replace `None` with a default value (e.g. '')
default_value = ''

# Use `coalesce` to replace `None` with the default value
joined_df = (airports_silver
             .join(airport_weather_silver.withColumn('NAME_DROP', coalesce(col('NAME_DROP'), lit(default_value))), 
                   airports_silver.NAME == airport_weather_silver.NAME_DROP, 'left')
            )

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
<command-380894863128637> in <cell line: 15>()
     13 
     14 # Use `coalesce` to replace `None` with the default value
---> 15 joined_df = (airports_silver
     16              .join(airport_weather_silver.withColumn('NAME_DROP', coalesce(col('NAME_DROP'), lit(default_value))), 
     17                    airports_silver.NAME == airport_weather_silver.NAME_DROP, 'left')

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - start, signature

/databricks/spark/python/pyspark/sql/dataframe.py in join(self, other, on, how)
   1623                 on =

Our two data tables have now been transformed and prepped for further analysis. Before moving on, we'll write the transformed data files into Delta Tables - Silver Layer

In [0]:
df = spark.createDataFrame([])
df.write.format("delta").mode("overwrite").save("/user/hive/warehouse/silver")

---------------------------------------------------------------------------
ValueError                                Traceback (most recent call last)
<command-4130278207381105> in <cell line: 1>()
----> 1 df = spark.createDataFrame([])
      2 df.write.format("delta").mode("overwrite").save("/user/hive/warehouse/silver")

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - start, signature

/databricks/spark/python/pyspark/sql/session.py in createDataFrame(self, data, schema, samplingRatio, verifySchema)
    970                 data, schema, samplingRatio, verifySchema
    971             )
--> 972         return self._create_dataframe(
    973             data, schema, samplingRatio, verifySchem

In [0]:
airport_weather_silver.write.mode("overwrite").format("delta").option("inferSchema", "true").save("/dbfs/warehouse/default.db/silver")

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
<command-4130278207381106> in <cell line: 1>()
----> 1 airport_weather_silver.write.mode("overwrite").format("delta").option("inferSchema", "true").save("/dbfs/warehouse/default.db/silver")

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - start, signature

/databricks/spark/python/pyspark/sql/readwriter.py in save(self, path, format, mode, partitionBy, **options)
    966             self._jwrite.save()
    967         else:
--> 968             self._jwrite.save(path)
    969 
    970     @since(1.4)

/databricks/spark/python/lib/py4j-0.10.9.5-sr

In [0]:
%sql
-- CREATE OR REPLACE TABLE AS
SELECT * FROM airport_weather_silver

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
<command-4130278207381108> in <cell line: 1>()
      5     display(df)
      6     return df
----> 7   _sqldf = ____databricks_percent_sql()
      8 finally:
      9   del ____databricks_percent_sql

<command-4130278207381108> in ____databricks_percent_sql()
      2   def ____databricks_percent_sql():
      3     import base64
----> 4     df = spark.sql(base64.standard_b64decode("U0VMRUNUICogRlJPTSBhaXJwb3J0X3dlYXRoZXJfc2lsdmVy").decode())
      5     display(df)
      6     return df

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - start, signa

In [0]:
#write new transformed dataframes to delta table 
airports_silver.write.mode("overwrite").format("delta").saveAsTable("airport_data_silver")
airport_weather_silver.write.mode("overwrite").format("delta").saveAsTable("airport_weather_silver")

In [0]:
display(spark.catalog.listTables("default"))

---------------------------------------------------------------------------
ValueError                                Traceback (most recent call last)
<command-680632833991804> in <cell line: 1>()
----> 1 display(spark.catalog.listTables("default"))

/databricks/python_shell/dbruntime/display.py in display(self, input, *args, **kwargs)
     84 
     85         elif isinstance(input, list):
---> 86             self.display(self.sparkSession.createDataFrame(input))
     87         elif type(input).__module__ == 'pandas.core.frame' and type(input).__name__ == 'DataFrame':
     88             self.display(self.sparkSession.createDataFrame(input))

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - st

In [0]:
# Create a view or table

temp_table_name = "airport_weather_2020_csv"

df.createOrReplaceTempView(temp_table_name)

In [0]:
%sql

/* Query the created temp table in a SQL cell */

select * from `airport_weather_2020_csv`

In [0]:
# With this registered as a temp view, it will only be available to this particular notebook. If you'd like other users to be able to query this table, you can also create a table from the DataFrame.
# Once saved, this table will persist across cluster restarts as well as allow various users across different notebooks to query this data.
# To do so, choose your table name and uncomment the bottom line.

permanent_table_name = "airport_weather_2020_csv"

# df.write.format("parquet").saveAsTable(permanent_table_name)

##Recycling Bin

In [0]:
#ensure correct data type after transformating our initial table
airport_weather_silver = (airport_weather_silver
                  .withColumn("PRCP_MM", col('PRCP_MM').cast(FloatType()))
                  .withColumn("SNOW_MM", col('SNOW_MM').cast(FloatType()))
                  .withColumn("SNWD_MM", col('SNWD_MM').cast(FloatType()))
                  .withColumn("TAVG_C", col('TAVG_C').cast(FloatType()))
                  .withColumn("TMAX_C", col('TMAX_C').cast(FloatType()))
                  .withColumn("TMIN_C", col('TMIN_C').cast(FloatType()))
                 )